In [ ]:
import numpy as np
import os,time
from astropy.nddata import CCDData
import ccdproc
from astropy.io import fits

In [ ]:
def imlist(fname,ext='.fits'):
    # ensures all files have requested extension
    imnames=open(fname,'r').readlines()
    imnames=[s.replace('\n','') for s in imnames]    
    imnames=[s.replace(ext,'') for s in imnames]
    imnames=[s+ext for s in imnames]
    return imnames

### Enter Data Directory and Flat Field Name

In [ ]:
datadir = '/home/astrotech1/Desktop/M101/Bdata'
flatfile='SkyFlat2009B.fits'
os.chdir(datadir)

**Read individual zero images and combine into master zero**

In [ ]:
zerofiles=imlist('zeros.lis')

st=time.time()
zeros=[]
for zerofile in zerofiles:
    image=CCDData.read(zerofile, unit="adu")
    zeros.append(image)
et=time.time()
print('Reading: {:.1f} sec'.format(et-st))
    
combiner = ccdproc.Combiner(zeros)
st=time.time()
combiner.sigma_clipping(low_thresh=3, high_thresh=3)
et=time.time()
print('Clipping: {:.1f} sec'.format(et-st))

st=time.time()
combined = combiner.average_combine()
et=time.time()
print('Combining: {:.1f} sec'.format(et-st))
            
    
hdu = fits.PrimaryHDU(combined.data.astype(np.float32),
                      header=image.header)
hdu.writeto('Zero.fits',overwrite=True)
print('Finished')

**Read images, subtract master zero, divide by flat field**

In [ ]:
zerofile='Zero.fits'
zero=CCDData.read(zerofile, unit="adu")
flat=CCDData.read(flatfile, unit='adu')
imfiles=imlist('images.lis')

st=time.time()
for imfile in imfiles:
    print('Working on {}'.format(imfile))
    image=CCDData.read(imfile, unit="adu")
    image.data -= zero.data
    image.header['ZEROSUB']=zerofile
    image.data /= flat.data
    image.header['ZEROSUB']=flatfile
    image.write('r'+imfile,overwrite=True)

et=time.time()
print('Processing: {:.1f} sec'.format(et-st))
            